In [1]:
import os
import random
import copy
import time
import sys
import shutil
import argparse
import errno
import math
import numpy as np
from collections import defaultdict, OrderedDict
import tensorboardX
from tqdm import tqdm
import pickle as pkl

import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from torch.utils.data import DataLoader
from torch.optim.lr_scheduler import StepLR

from lib.utils.tools import *
from lib.model.loss import *
from lib.model.loss_mesh import *
from lib.utils.utils_mesh import *
from lib.utils.utils_smpl import *
from lib.utils.utils_data import *
from lib.utils.learning import *
from lib.data.dataset_mesh import MotionSMPL
from lib.model.model_mesh import MeshRegressor
from torch.utils.data import DataLoader

import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D

import torch.multiprocessing as mp
mp.set_start_method('spawn', force=True)

import torch
import numpy as np
import glob
import os
import io
import random
import pickle
from torch.utils.data import Dataset, DataLoader
from lib.data.augmentation import Augmenter3D
from lib.utils.tools import read_pkl
from lib.utils.utils_data import flip_data, crop_scale
from lib.utils.utils_mesh import flip_thetas
from lib.utils.utils_smpl import SMPL
from torch.utils.data import Dataset, DataLoader
from lib.data.datareader_h36m import DataReaderH36M  
from lib.data.datareader_mesh import DataReaderMesh  
from lib.data.dataset_action import random_move  

In [2]:
### THIS SCRIPT IS USED TO EVALUATE THE PREDICTED SMPL VERTICES

In [3]:
# Example input (assuming you have data in the same format)
# batched_array_test_outputs = [{'theta': ..., 'verts': ..., 'kp_3d': ...}, ...]
SAVE_FILE = False
DATASET_TYPE = 'test'

In [4]:
def parse_args():
    parser = argparse.ArgumentParser()
    parser.add_argument("--config", type=str, default="configs/pretrain.yaml", help="Path to the config file.")
    parser.add_argument('-c', '--checkpoint', default='checkpoint', type=str, metavar='PATH', help='checkpoint directory')
    parser.add_argument('-p', '--pretrained', default='checkpoint', type=str, metavar='PATH', help='pretrained checkpoint directory')
    parser.add_argument('-r', '--resume', default='', type=str, metavar='FILENAME', help='checkpoint to resume (file name)')
    parser.add_argument('-e', '--evaluate', default='', type=str, metavar='FILENAME', help='checkpoint to evaluate (file name)')
    parser.add_argument('-freq', '--print_freq', default=100)
    parser.add_argument('-ms', '--selection', default='latest_epoch.bin', type=str, metavar='FILENAME', help='checkpoint to finetune (file name)')
    parser.add_argument('-sd', '--seed', default=0, type=int, help='random seed')
    opts = parser.parse_args()
    return opts

In [5]:
with open(r'data/mesh/mesh_det_pw3d.pkl', 'rb') as f:
    dataset_pw3d = pkl.load(f)

In [6]:


# Ground truth is in the following order

if DATASET_TYPE == 'test':
    # Assuming dataset_pw3d['test']['source'] is your list
    source_list = dataset_pw3d['test']['source']
elif DATASET_TYPE == 'train':
    source_list = dataset_pw3d['train']['source']

# Create an ordered set (preserving order of first appearance)
gt_order = list(dict.fromkeys(source_list))

# The result is in the form of a list
gt_order

['downtown_arguing_000',
 'downtown_bar_000',
 'downtown_bus_000',
 'downtown_cafe_000',
 'downtown_car_000',
 'downtown_crossStreets_000',
 'downtown_downstairs_000',
 'downtown_enterShop_000',
 'downtown_rampAndStairs_000',
 'downtown_runForBus_000',
 'downtown_runForBus_010',
 'downtown_sitOnStairs_000',
 'downtown_stairs_000',
 'downtown_upstairs_000',
 'downtown_walkBridge_010',
 'downtown_walkUphill_000',
 'downtown_walking_000',
 'downtown_warmWelcome_000',
 'downtown_weeklyMarket_000',
 'downtown_windowShopping_000',
 'flat_guitar_010',
 'flat_packBags_000',
 'office_phoneCall_000',
 'outdoors_fencing_010',
 'downtown_arguing_001',
 'downtown_bar_001',
 'downtown_bus_001',
 'downtown_cafe_001',
 'downtown_car_001',
 'downtown_crossStreets_001',
 'downtown_rampAndStairs_001',
 'downtown_runForBus_001',
 'downtown_runForBus_011',
 'downtown_sitOnStairs_001',
 'downtown_walking_001',
 'downtown_warmWelcome_001',
 'office_phoneCall_001']

In [7]:
# Predictions are in the following order
ordered_unique_list = list(dict.fromkeys(source_list))

predictions_order = sorted(ordered_unique_list)
predictions_order2 = predictions_order.copy()

if DATASET_TYPE == 'test':
    # Move element at index 25 to index 27
    element = predictions_order.pop(25)  # Remove the element at index 25
    predictions_order.insert(27, element)  # Insert it at index 27

predictions_order


['downtown_arguing_000',
 'downtown_arguing_001',
 'downtown_bar_000',
 'downtown_bar_001',
 'downtown_bus_000',
 'downtown_bus_001',
 'downtown_cafe_000',
 'downtown_cafe_001',
 'downtown_car_000',
 'downtown_car_001',
 'downtown_crossStreets_000',
 'downtown_crossStreets_001',
 'downtown_downstairs_000',
 'downtown_enterShop_000',
 'downtown_rampAndStairs_000',
 'downtown_rampAndStairs_001',
 'downtown_runForBus_000',
 'downtown_runForBus_001',
 'downtown_runForBus_010',
 'downtown_runForBus_011',
 'downtown_sitOnStairs_000',
 'downtown_sitOnStairs_001',
 'downtown_stairs_000',
 'downtown_upstairs_000',
 'downtown_walkBridge_010',
 'downtown_walking_000',
 'downtown_walking_001',
 'downtown_walkUphill_000',
 'downtown_warmWelcome_000',
 'downtown_warmWelcome_001',
 'downtown_weeklyMarket_000',
 'downtown_windowShopping_000',
 'flat_guitar_010',
 'flat_packBags_000',
 'office_phoneCall_000',
 'office_phoneCall_001',
 'outdoors_fencing_010']

In [8]:
def create_mapping(predictions_order, gt_order):
    """
    Create a mapping from predictions_order to gt_order.
    """
    mapping = {}
    for i, val in enumerate(predictions_order):
        mapping[i] = gt_order.index(val)
    return mapping

def reorder_list(input_list, mapping):
    # Create an output list of the same length as input_list
    output_list = [None] * len(input_list)
    
    # Reorder elements according to the mapping
    for old_index, new_index in mapping.items():
        output_list[new_index] = input_list[old_index]
    
    return output_list

In [9]:
mapping = create_mapping(predictions_order, gt_order)

In [10]:
reordered_list = reorder_list(predictions_order, mapping)

In [11]:
gt_order == reordered_list

True

In [12]:
import os
import numpy as np

def count_total_frames(base_path):
    """
    Recursively counts the total number of frames from vertices_all_frames.npy
    files in person_1 and person_2 folders.

    Parameters:
        base_path (str): The root folder path where the search begins.

    Returns:
        int: The total number of frames summed across all files.
    """
    total_frames = 0  # Initialize total frame counter

    # Walk through all subdirectories in the base_path
    for root, dirs, files in os.walk(base_path):
        # Check if we're in a person_1 or person_2 folder
        if os.path.basename(root) in ['person_1', 'person_2']:
            # Check if 'vertices_all_frames.npy' exists in the current folder
            file_path = os.path.join(root, 'vertices.npy') ##########################
            if os.path.isfile(file_path):
                try:
                    # Load the numpy array and get the number of frames (first dimension)
                    vertices_data = np.load(file_path)
                    nr_frames = vertices_data.shape[0]  # First dimension is number of frames
                    total_frames += nr_frames
                    print(f"Found file: {file_path} | Frames: {nr_frames}")
                except Exception as e:
                    print(f"Error loading file {file_path}: {e}")

    print(f"\nTotal number of frames: {total_frames}")
    return total_frames



# Define the base folder path to search in
if DATASET_TYPE == 'test':
    base_folder = r"E:\Users\Philipp\Dokumente\Pose_Estimation_3D\Alphapose\AlphaPose\examples\res\test_set"
elif DATASET_TYPE == 'train':
    base_folder = r"E:\Users\Philipp\Dokumente\Pose_Estimation_3D\Alphapose\AlphaPose\examples\res\train_set"
elif DATASET_TYPE == 'val':
    base_folder = r"E:\Users\Philipp\Dokumente\Pose_Estimation_3D\Alphapose\AlphaPose\examples\res\val_set"

# Run the frame counting function
total_frames = count_total_frames(base_folder)


Found file: E:\Users\Philipp\Dokumente\Pose_Estimation_3D\Alphapose\AlphaPose\examples\res\test_set\downtown_arguing_00\MotionBert\person_1\vertices.npy | Frames: 898
Found file: E:\Users\Philipp\Dokumente\Pose_Estimation_3D\Alphapose\AlphaPose\examples\res\test_set\downtown_arguing_00\MotionBert\person_2\vertices.npy | Frames: 895
Found file: E:\Users\Philipp\Dokumente\Pose_Estimation_3D\Alphapose\AlphaPose\examples\res\test_set\downtown_bar_00\MotionBert\person_1\vertices.npy | Frames: 1252
Found file: E:\Users\Philipp\Dokumente\Pose_Estimation_3D\Alphapose\AlphaPose\examples\res\test_set\downtown_bar_00\MotionBert\person_2\vertices.npy | Frames: 1206
Found file: E:\Users\Philipp\Dokumente\Pose_Estimation_3D\Alphapose\AlphaPose\examples\res\test_set\downtown_bus_00\MotionBert\person_1\vertices.npy | Frames: 1066
Found file: E:\Users\Philipp\Dokumente\Pose_Estimation_3D\Alphapose\AlphaPose\examples\res\test_set\downtown_bus_00\MotionBert\person_2\vertices.npy | Frames: 1482
Found file

In [13]:
config = 'configs/mesh/MB_train_pw3d.yaml'
args = get_config(config)


trainloader_params = {
        'batch_size': args.batch_size,
        'shuffle': False,
        'num_workers': 0,
        'pin_memory': True,
}
testloader_params = {
        'batch_size': args.batch_size,
        'shuffle': False,
        'num_workers': 0,
        'pin_memory': True,
}

In [14]:

class SMPLDataset(Dataset):
    def __init__(self, args, data_split, dataset): # data_split: train/test; dataset: h36m, coco, pw3d
        random.seed(0)
        np.random.seed(0)
        self.clip_len = args.clip_len
        self.data_split = data_split
    
        if dataset=="h36m":
            datareader = DataReaderH36M(n_frames=self.clip_len, sample_stride=args.sample_stride, data_stride_train=args.data_stride, data_stride_test=self.clip_len, dt_root=args.data_root, dt_file=args.dt_file_h36m)
        elif dataset=="coco":
            datareader = DataReaderMesh(n_frames=1, sample_stride=args.sample_stride, data_stride_train=1, data_stride_test=1, dt_root=args.data_root, dt_file=args.dt_file_coco, res=[640, 640])
        elif dataset=="pw3d":
            datareader = DataReaderMesh(n_frames=self.clip_len, sample_stride=args.sample_stride, data_stride_train=args.data_stride, data_stride_test=self.clip_len, dt_root=args.data_root, dt_file=args.dt_file_pw3d, res=[1920, 1920])
        else:
            raise Exception("Mesh dataset undefined.")
        self.datareader = datareader

        split_id_train, split_id_test = datareader.get_split_id()                        # Index of clips
        # print("ID TRAIN:")
        # print(split_id_train)
        print("ID TEST:")
        print(split_id_test)
        train_data, test_data = datareader.read_2d()
        train_data, test_data = train_data[split_id_train], test_data[split_id_test]     # Input: (N, T, 17, 3)
        self.motion_2d = {'train': train_data, 'test': test_data}[data_split]

        dt = datareader.dt_dataset
        smpl_pose_train = dt['train']['smpl_pose'][split_id_train]                       # (N, T, 72)
        smpl_shape_train = dt['train']['smpl_shape'][split_id_train]                     # (N, T, 10)
        smpl_pose_test = dt['test']['smpl_pose'][split_id_test]                          # (N, T, 72)
        smpl_shape_test = dt['test']['smpl_shape'][split_id_test]                        # (N, T, 10)

        source_list = dt['test']['source']

        # Create an ordered set (preserving order of first appearance)
        #ordered_set = list(dict.fromkeys(source_list))

        # The result is in the form of a list
        print(source_list)

                
        self.motion_smpl_3d = {'train': {'pose': smpl_pose_train, 'shape': smpl_shape_train}, 'test': {'pose': smpl_pose_test, 'shape': smpl_shape_test}}[data_split]
        self.smpl = SMPL(
            args.data_root,
            batch_size=1,
        )
    def get_split_id(self, datareader):
        return datareader.get_split_id()

    def __len__(self):
        'Denotes the total number of samples'
        return len(self.motion_2d)

    def __getitem__(self, index):
        raise NotImplementedError 

class MotionSMPL(SMPLDataset):
    def __init__(self, args, data_split, dataset):
        super(MotionSMPL, self).__init__(args, data_split, dataset)
        self.flip = args.flip
    
        
    def __getitem__(self, index):
        'Generates one sample of data'
        # Select sample
        motion_2d = self.motion_2d[index]                                            # motion_2d: (T,17,3)     
        motion_2d[:,:,2] = np.clip(motion_2d[:,:,2], 0, 1)
        motion_smpl_pose = self.motion_smpl_3d['pose'][index].reshape(-1, 24, 3)     # motion_smpl_3d: (T, 24, 3)    
        motion_smpl_shape = self.motion_smpl_3d['shape'][index]                      # motion_smpl_3d: (T,10)    
        
        # if self.data_split=="train":
        #     if self.flip and random.random() > 0.5:                                  # Training augmentation - random flipping
        #         motion_2d = flip_data(motion_2d)
        #         motion_smpl_pose = flip_thetas(motion_smpl_pose)                

            
        motion_smpl_pose = torch.from_numpy(motion_smpl_pose).reshape(-1, 72).float()
        motion_smpl_shape = torch.from_numpy(motion_smpl_shape).reshape(-1, 10).float()
        motion_smpl = self.smpl(
            betas=motion_smpl_shape,
            body_pose=motion_smpl_pose[:, 3:],
            global_orient=motion_smpl_pose[:, :3],
            pose2rot=True
        )
        motion_verts = motion_smpl.vertices.detach()*1000.0
        J_regressor = self.smpl.J_regressor_h36m
        J_regressor_batch = J_regressor[None, :].expand(motion_verts.shape[0], -1, -1).to(motion_verts.device)
        motion_3d_reg = torch.matmul(J_regressor_batch, motion_verts)                 # motion_3d: (T,17,3)  
        motion_verts = motion_verts - motion_3d_reg[:, :1, :]
        motion_3d_reg = motion_3d_reg - motion_3d_reg[:, :1, :]                       # motion_3d: (T,17,3)    
        motion_theta = torch.cat((motion_smpl_pose, motion_smpl_shape), -1)
        motion_smpl_3d = {
            'theta': motion_theta,       # smpl pose and shape
            'kp_3d': motion_3d_reg,      # 3D keypoints
            'verts': motion_verts,       # 3D mesh vertices
        }
        return motion_2d, motion_smpl_3d

In [15]:
mesh_train_pw3d = MotionSMPL(args, data_split='train', dataset="pw3d")
train_loader_pw3d = DataLoader(mesh_train_pw3d, **testloader_params)

mesh_val_pw3d = MotionSMPL(args, data_split='test', dataset="pw3d")
test_loader_pw3d = DataLoader(mesh_val_pw3d, **testloader_params)

ID TEST:
[range(0, 16), range(16, 32), range(32, 48), range(48, 64), range(64, 80), range(80, 96), range(96, 112), range(112, 128), range(128, 144), range(144, 160), range(160, 176), range(176, 192), range(192, 208), range(208, 224), range(224, 240), range(240, 256), range(256, 272), range(272, 288), range(288, 304), range(304, 320), range(320, 336), range(336, 352), range(352, 368), range(368, 384), range(384, 400), range(400, 416), range(416, 432), range(432, 448), range(448, 464), range(464, 480), range(480, 496), range(496, 512), range(512, 528), range(528, 544), range(544, 560), range(560, 576), range(576, 592), range(592, 608), range(608, 624), range(624, 640), range(640, 656), range(656, 672), range(672, 688), range(688, 704), range(704, 720), range(720, 736), range(736, 752), range(752, 768), range(768, 784), range(784, 800), range(800, 816), range(816, 832), range(832, 848), range(848, 864), range(864, 880), range(880, 896), range(898, 914), range(914, 930), range(930, 946), r

In [16]:
def main():
    mesh_train_pw3d = MotionSMPL(args, data_split='train', dataset="pw3d")
    train_loader_pw3d = DataLoader(mesh_train_pw3d, **trainloader_params)

    mesh_val_pw3d = MotionSMPL(args, data_split='test', dataset="pw3d")
    test_loader_pw3d = DataLoader(mesh_val_pw3d, **testloader_params)

# Call the main function
main()



ID TEST:
[range(0, 16), range(16, 32), range(32, 48), range(48, 64), range(64, 80), range(80, 96), range(96, 112), range(112, 128), range(128, 144), range(144, 160), range(160, 176), range(176, 192), range(192, 208), range(208, 224), range(224, 240), range(240, 256), range(256, 272), range(272, 288), range(288, 304), range(304, 320), range(320, 336), range(336, 352), range(352, 368), range(368, 384), range(384, 400), range(400, 416), range(416, 432), range(432, 448), range(448, 464), range(464, 480), range(480, 496), range(496, 512), range(512, 528), range(528, 544), range(544, 560), range(560, 576), range(576, 592), range(592, 608), range(608, 624), range(624, 640), range(640, 656), range(656, 672), range(672, 688), range(688, 704), range(704, 720), range(720, 736), range(736, 752), range(752, 768), range(768, 784), range(784, 800), range(800, 816), range(816, 832), range(832, 848), range(848, 864), range(864, 880), range(880, 896), range(898, 914), range(914, 930), range(930, 946), r

In [17]:
split_id_train, split_id_test = mesh_train_pw3d.get_split_id(mesh_train_pw3d.datareader)

In [18]:
total_length = 0

for ran in split_id_test:
    total_length += len(ran)

avg_len = total_length / len(split_id_test)

print(avg_len)
print(total_length)

16.0
35232


In [19]:
len(mesh_val_pw3d[0][1]['theta'])

16

In [20]:
# sum = 0
# for i in range(len(mesh_train_pw3d)):
#     sum += len(mesh_train_pw3d[i][1]['theta'])
# print(sum)


In [21]:
len(mesh_train_pw3d)

2794

In [22]:
# THE REASON FOR WHY NWE DONT HAVE 35515 ELEMS IN THE TEST SET mesh_val... but 35232 is split_id_test, which FILTERS OUT SOME

In [23]:
# retrieves the ground truth coords for any image 

def get_frame_coords(dataset:str, file_name: str, frame_number: int, split_id_train, mesh_train_pw3d):
    index = None
    resulting_coords = None  # Initialize resulting_coords to avoid potential errors
    
    # Find the first appearance of the file_name
    if dataset == 'train':
        img_names = dataset_pw3d["train"]["source"]
    else:
        img_names = dataset_pw3d["test"]["source"]

    for idx, file in enumerate(img_names):
        if file == file_name:
            index = idx
            break  # Exit the loop as soon as the file is found
    else:
        # This executes if no break occurs in the loop (file not found)
        print("File not found")
        return None, None

    # Calculate the target frame number
    target_number = index + frame_number
    
    # Find the range index
    range_index = next((i for i, r in enumerate(split_id_train) if r.start <= target_number < r.stop), None)
    
    if range_index is not None:
        print(f"The number {target_number} is in range at index {range_index}: {split_id_train[range_index]}")
        # Calculate the index inside the range
        range_start = split_id_train[range_index].start
        index_in_range = target_number - range_start
        
        # Access the batch and ensure indices are valid
        if range_index < len(mesh_train_pw3d) and index_in_range < len(mesh_train_pw3d[range_index][1]['kp_3d']):
            resulting_coords = mesh_train_pw3d[range_index][1]['kp_3d'][index_in_range]
        else:
            print(f"Index {index_in_range} is out of bounds for range index {range_index}.")
    else:
        print(f"The number {target_number} is not in any range of split_id_train.")
        return None, None

    return resulting_coords


In [24]:
resulting_coords = get_frame_coords("test", 'downtown_arguing_000', 2, split_id_test, mesh_val_pw3d)

The number 2 is in range at index 0: range(0, 16)


### EVALUATION


### Testing backpack example

In [25]:
J_regressor_motionbert = np.load("Joint_regressor/J_regressor_h36m_correct.npy")


def thetas_to_kp_3d(pred_thetas, pred_verts, J_regressor):
    pred_thetas = np.concatenate([pred_thetas, np.zeros(10)])
    pred_kp_3d = J_regressor @ pred_verts


    # Define the rotation matrix for -180 degrees around the x-axis
    R_x = np.array([
        [1,  0,  0],
        [0, -1,  0],
        [0,  0, -1]
    ])

    # Rotate each point by applying the rotation matrix
    pred_kp_3d = pred_kp_3d @ R_x.T

    

In [26]:
# pred_thetas = np.load('Prediction_necessities/all_thetas_backpack.npy')[0]
# pred_thetas = np.concatenate([pred_thetas, np.zeros(10)])
# pred_verts = np.load('Prediction_necessities/vertices_backpack_frame_00_pred.npy')
# #J_regressor = J_regressor.to('cpu')
# pred_kp_3d = J_regressor_motionbert @ pred_verts


In [27]:
# # Define the rotation matrix for -180 degrees around the x-axis
# R_x = np.array([
#     [1,  0,  0],
#     [0, -1,  0],
#     [0,  0, -1]
# ])

# # Rotate each point by applying the rotation matrix
# pred_kp_3d = pred_kp_3d @ R_x.T


In [28]:
# # Extract the first coordinate
# first_point = pred_kp_3d[0]

# # Translate all points to set the first point as the origin
# pred_kp_3d = pred_kp_3d - first_point

# # Ensure the first point is now exactly zero
# pred_kp_3d[0] = np.array([0.0, 0.0, 0.0])

In [29]:
# import torch

# pred_thetas = torch.tensor(pred_thetas).unsqueeze(0).unsqueeze(0)
# pred_verts = torch.tensor(pred_verts).unsqueeze(0).unsqueeze(0)
# pred_kp_3d = torch.tensor(pred_kp_3d).unsqueeze(0).unsqueeze(0)

# device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# # Move tensors to GPU
# pred_thetas = pred_thetas.to(device)
# pred_verts = pred_verts.to(device)
# pred_kp_3d = pred_kp_3d.to(device)



In [30]:
# sample_prediction = {
#     "theta": pred_thetas,
#     "kp_3d": pred_kp_3d,
#     "verts": pred_verts,
# }

In [31]:
# pred_kp_3d.shape

In [32]:
# batch = next(iter(train_loader_pw3d))

In [33]:
# # These two are the same 
# mesh_train_pw3d[94][1]['kp_3d'][0]
# batch[1]['kp_3d'][94][0]

In [34]:
# get_frame_coords("train", 'courtyard_backpack_000', 0, split_id_train, mesh_train_pw3d)

In [35]:
# sample_prediction["theta"].shape

In [36]:
# # Extract, reshape, and convert batch[0]
# batch[0] = batch[0][0][0]
# batch[0] = torch.tensor(batch[0]).unsqueeze(0).unsqueeze(0).to(device)

# # Extract, reshape, and convert batch[1] elements
# batch[1]['theta'] = torch.tensor(batch[1]['theta'][0][0]).unsqueeze(0).unsqueeze(0).to(device)
# batch[1]['kp_3d'] = torch.tensor(batch[1]['kp_3d'][0][0]).unsqueeze(0).unsqueeze(0).to(device)
# batch[1]['verts'] = torch.tensor(batch[1]['verts'][0][0]).unsqueeze(0).unsqueeze(0).to(device)

In [37]:
# "output is a dict of shape"
# theta: (1, T, dim_theta) (e.g., (1, T, 72))
# verts: (1, T, num_verts, 3) (e.g., (1, T, 6890, 3) if num_verts=6890)
# kp_3d: (1, T, 17, 3)



def validate(criterion, dataset_name='h36m'):

    print(f'===========> validating {dataset_name}')
    batch_time = AverageMeter()
    losses = AverageMeter()
    losses_dict = {'loss_3d_pos': AverageMeter(), 
                   'loss_3d_scale': AverageMeter(), 
                   'loss_3d_velocity': AverageMeter(),
                   'loss_lv': AverageMeter(), 
                   'loss_lg': AverageMeter(), 
                   'loss_a': AverageMeter(), 
                   'loss_av': AverageMeter(), 
                   'loss_pose': AverageMeter(), 
                   'loss_shape': AverageMeter(),
                   'loss_norm': AverageMeter(),
    }
    mpjpes = AverageMeter()
    mpves = AverageMeter()
    results = defaultdict(list)
    smpl = SMPL(args.data_root, batch_size=1).cuda()
    J_regressor = smpl.J_regressor_h36m
    with torch.no_grad():
        end = time.time()
    ######################################################################
    idx = 0
    batch_input = batch[0]
    batch_gt = batch[1]

    batch_size, clip_len = batch_input.shape[:2]
    if torch.cuda.is_available():
        batch_gt['theta'] = batch_gt['theta'].cuda().float()
        batch_gt['kp_3d'] = batch_gt['kp_3d'].cuda().float()
        batch_gt['verts'] = batch_gt['verts'].cuda().float()
        batch_input = batch_input.cuda().float()

    output = [sample_prediction]
    

    output_final = output

    print('Pred is')
    print(output[0]['kp_3d'].shape)

    print('GT is')
    print(batch_gt['kp_3d'].shape)


    loss_dict = criterion(output, batch_gt)
    
    loss = args.lambda_3d      * loss_dict['loss_3d_pos']      + \
        args.lambda_scale   * loss_dict['loss_3d_scale']    + \
        args.lambda_3dv     * loss_dict['loss_3d_velocity'] + \
        args.lambda_lv      * loss_dict['loss_lv']          + \
        args.lambda_lg      * loss_dict['loss_lg']          + \
        args.lambda_a       * loss_dict['loss_a']           + \
        args.lambda_av      * loss_dict['loss_av']          + \
        args.lambda_shape   * loss_dict['loss_shape']       + \
        args.lambda_pose    * loss_dict['loss_pose']        + \
        args.lambda_norm    * loss_dict['loss_norm'] 
    # update metric
    losses.update(loss.item(), batch_size)
    loss_str = ''
    for k, v in loss_dict.items():
        losses_dict[k].update(v.item(), batch_size)
        loss_str += '{0} {loss.val:.3f} ({loss.avg:.3f})\t'.format(k, loss=losses_dict[k])
    mpjpe, mpve = compute_error(output, batch_gt)
    mpjpes.update(mpjpe, batch_size)
    mpves.update(mpve, batch_size)
    
    for keys in output[0].keys():
        if type(output[0][keys]) != np.ndarray: 
            output[0][keys] = output[0][keys].detach().cpu().numpy()
        if type(batch_gt[keys]) != np.ndarray: 
            batch_gt[keys] = batch_gt[keys].detach().cpu().numpy()
    results['kp_3d'].append(output[0]['kp_3d'])
    results['verts'].append(output[0]['verts'])
    results['kp_3d_gt'].append(batch_gt['kp_3d'])
    results['verts_gt'].append(batch_gt['verts'])

    # measure elapsed time
    batch_time.update(time.time() - end)
    end = time.time()

    if idx % int(100) == 0:
        print('Test: [{0}/{1}]\t'
            'Time {batch_time.val:.3f} ({batch_time.avg:.3f})\t'
            'Loss {loss.val:.4f} ({loss.avg:.4f})\t'
            '{2}'
            'PVE {mpves.val:.3f} ({mpves.avg:.3f})\t'
            'JPE {mpjpes.val:.3f} ({mpjpes.avg:.3f})'.format(
            idx, 1, loss_str, batch_time=batch_time,
            loss=losses, mpves=mpves, mpjpes=mpjpes))
           ###################################################################

    print(f'==> start concating results of {dataset_name}')
    for term in results.keys():
        results[term] = np.concatenate(results[term])
    print(f'==> start evaluating {dataset_name}...')
    error_dict = evaluate_mesh(results)
    err_str = ''
    for err_key, err_val in error_dict.items():
        err_str += '{}: {:.2f}mm \t'.format(err_key, err_val)
    print(f'=======================> {dataset_name} validation done: ', loss_str)
    print(f'=======================> {dataset_name} validation done: ', err_str)
    return losses.avg, error_dict['mpjpe'], error_dict['pa_mpjpe'], error_dict['mpve'], losses_dict

In [38]:
# test_loss, test_mpjpe, test_pa_mpjpe, test_mpve, test_losses_dict = validate(criterion=criterion, dataset_name='3dpw')

In [39]:
# Next: pipeline to predict all images and then get values (test set)

In [40]:
# # Output should be a list of these

# sample_prediction = {
#     "theta": pred_thetas,
#     "kp_3d": pred_kp_3d,
#     "verts": pred_verts,
# }

# # Afterwards, check if they have the sae order as the GT

In [41]:
###################################################
###################################################
###################################################

In [42]:
#thetas_arguing = np.load(r"E:\Users\Philipp\Dokumente\Pose_Estimation_3D\Alphapose\AlphaPose\examples\res\test_set\downtown_arguing_00\MotionBert\all_thetas.npy")

In [43]:
#result_params = np.concatenate([thetas_arguing[0], np.zeros(84)])


In [44]:
#result_params

In [45]:
# Base directory paths
dataset_dir = r'E:\Users\Philipp\Dokumente\Pose_Estimation_3D\3DPW'
base_pred_dir = r'E:\Users\Philipp\Dokumente\Pose_Estimation_3D\Alphapose\AlphaPose\examples\res\test_set'
sequence_folders = [f for f in os.listdir(base_pred_dir) if os.path.isdir(os.path.join(base_pred_dir, f))]

In [46]:
## CALCULATE ALL EVALUATION DICTIONARIES FOR ONE PERSON OF A SEQUENCE



J_regressor_motionbert = np.load("Joint_regressor/J_regressor_h36m_correct.npy")



all_pred_thetas = np.load(r"E:\Users\Philipp\Dokumente\Pose_Estimation_3D\Alphapose\AlphaPose\examples\res\test_set\downtown_arguing_00\MotionBert\person_1\all_thetas.npy")
#all_pred_thetas = np.concatenate([pred_thetas, np.zeros(10)])
all_pred_verts = np.load(r"E:\Users\Philipp\Dokumente\Pose_Estimation_3D\Alphapose\AlphaPose\examples\res\test_set\downtown_arguing_00\MotionBert\person_1\vertices_all_frames.npy")
#J_regressor = J_regressor.to('cpu')
#all_pred_kp_3d = J_regressor_motionbert @ pred_verts



def preds_to_dict(all_pred_thetas, all_pred_verts, J_regressor):
    all_outputs = []
    
    for i in range(len(all_pred_thetas)):
        pred_thetas = all_pred_thetas[i]
        pred_verts = all_pred_verts[i]

        pred_thetas = np.concatenate([pred_thetas, np.zeros(10)])
        pred_kp_3d = J_regressor @ pred_verts


        # Define the rotation matrix for -180 degrees around the x-axis
        R_x = np.array([
            [1,  0,  0],
            [0, -1,  0],
            [0,  0, -1]
        ])

        # Rotate each point by applying the rotation matrix
        pred_kp_3d = pred_kp_3d @ R_x.T


        # Extract the first coordinate
        first_point = pred_kp_3d[0]

        # Translate all points to set the first point as the origin
        pred_kp_3d = pred_kp_3d - first_point

        # Ensure the first point is now exactly zero
        pred_kp_3d[0] = np.array([0.0, 0.0, 0.0])


        # pred_thetas = torch.tensor(pred_thetas).unsqueeze(0).unsqueeze(0)
        # pred_verts = torch.tensor(pred_verts).unsqueeze(0).unsqueeze(0)
        # pred_kp_3d = torch.tensor(pred_kp_3d).unsqueeze(0).unsqueeze(0)

        # device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

        # # Move tensors to GPU
        # pred_thetas = pred_thetas.to(device)
        # pred_verts = pred_verts.to(device)
        # pred_kp_3d = pred_kp_3d.to(device)


        sample_prediction = {
            "theta": pred_thetas,
            "kp_3d": pred_kp_3d * 1000,
            "verts": pred_verts,
        }

        all_outputs.append(sample_prediction)

    return(all_outputs)



In [47]:
def preds_to_lists(all_pred_thetas, all_pred_verts, J_regressor):
    pred_thetas_op = []
    pred_verts_op = []
    pred_kp3d_op = []
    
    for i in range(len(all_pred_thetas)):
        pred_thetas = all_pred_thetas[i]
        pred_verts = all_pred_verts[i]

        pred_thetas = np.concatenate([pred_thetas, np.zeros(10)])
        pred_kp_3d = J_regressor @ pred_verts


        # # Define the rotation matrix for -180 degrees around the x-axis
        # R_x = np.array([
        #     [1,  0,  0],
        #     [0, -1,  0],
        #     [0,  0, -1]
        # ])

        # # Rotate each point by applying the rotation matrix
        # pred_kp_3d = pred_kp_3d @ R_x.T


        # Extract the first coordinate
        first_point = pred_kp_3d[0]

        # Translate all points to set the first point as the origin
        pred_kp_3d = pred_kp_3d - first_point

        # Ensure the first point is now exactly zero
        pred_kp_3d[0] = np.array([0.0, 0.0, 0.0])


        # pred_thetas = torch.tensor(pred_thetas).unsqueeze(0).unsqueeze(0)
        # pred_verts = torch.tensor(pred_verts).unsqueeze(0).unsqueeze(0)
        # pred_kp_3d = torch.tensor(pred_kp_3d).unsqueeze(0).unsqueeze(0)

        device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

        # Move tensors to GPU
        # pred_thetas = pred_thetas.to(device)
        # pred_verts = pred_verts.to(device)
        # pred_kp_3d = pred_kp_3d.to(device)


        pred_thetas_op.append(pred_thetas)
        pred_verts_op.append(pred_verts)
        pred_kp3d_op.append(pred_kp_3d)

    return pred_thetas_op, pred_verts_op, pred_kp3d_op


In [48]:
all_sequence_outputs = preds_to_dict(all_pred_thetas, all_pred_verts, J_regressor_motionbert)

In [49]:
############
############
############
#
############

In [50]:
import os
import pickle as pkl

# Define the base directory and dataset directory
if DATASET_TYPE == 'test':
    base_dir = r"E:\Users\Philipp\Dokumente\Pose_Estimation_3D\Alphapose\AlphaPose\examples\res\test_set"
elif DATASET_TYPE == 'train':
    base_dir = r"E:\Users\Philipp\Dokumente\Pose_Estimation_3D\Alphapose\AlphaPose\examples\res\train_set"

# Get a list of all subfolders
subfolders = [f.path for f in os.scandir(base_dir) if f.is_dir()]
folders = []
test_outputs = []


print("Processing subfolders:")
for folder in subfolders:
    # Get the sequence name (basename of the folder)
    seq_name = os.path.basename(folder)
    
    # Construct the path to the .pkl file
    seq_file = os.path.join(dataset_dir, 'sequenceFiles', 'sequenceFiles', f'{DATASET_TYPE}', seq_name + '.pkl')
    
    # Check if the .pkl file exists
    if os.path.exists(seq_file):
        # Load the .pkl file
        with open(seq_file, 'rb') as file:
            seq = pkl.load(file, encoding='latin1')
        
        print(f"Loaded sequence for {seq_name}")
        
        # Check if the subfolder contains a 'MotionBert' folder
        motionbert_folder = os.path.join(folder, 'MotionBert')
        if os.path.exists(motionbert_folder) and os.path.isdir(motionbert_folder):
            # Create a list of "person_" folders inside the MotionBert folder
            person_folders = [
                os.path.join(motionbert_folder, d)
                for d in os.listdir(motionbert_folder)
                if os.path.isdir(os.path.join(motionbert_folder, d)) and d.startswith("person_")
            ]
            print(f"'{seq_name}' contains a 'MotionBert' folder with person folders:")
            for person_folder in person_folders:
                folders.append(person_folder)

                n_person = int(person_folder[-1])
                # Load the files
                vertices_path = os.path.join(person_folder, "vertices.npy") ####################
                thetas_path = os.path.join(person_folder, "all_thetas.npy")
                
                if os.path.exists(vertices_path) and os.path.exists(thetas_path):
                    all_pred_verts = np.load(vertices_path)
                    all_pred_thetas = np.load(thetas_path)
                    
                    mask = np.array(seq['campose_valid'][n_person-1])
                    all_pred_thetas = all_pred_thetas[mask == 1]

                    print(len(all_pred_thetas), len(all_pred_verts))

                    # Call the function
                    sequence_output = preds_to_dict(all_pred_thetas, all_pred_verts, J_regressor_motionbert) 
                    test_outputs.append(sequence_output)
    
        else:
            print(f"'{seq_name}' does NOT contain a 'MotionBert' folder.")
    else:
        print(f"Sequence file for {seq_name} does not exist: {seq_file}")


Processing subfolders:
Loaded sequence for downtown_arguing_00
'downtown_arguing_00' contains a 'MotionBert' folder with person folders:
898 898
895 895
Loaded sequence for downtown_bar_00
'downtown_bar_00' contains a 'MotionBert' folder with person folders:
1252 1252
1206 1206
Loaded sequence for downtown_bus_00
'downtown_bus_00' contains a 'MotionBert' folder with person folders:
1066 1066
1482 1482
Loaded sequence for downtown_cafe_00
'downtown_cafe_00' contains a 'MotionBert' folder with person folders:
934 934
1142 1142
Loaded sequence for downtown_car_00
'downtown_car_00' contains a 'MotionBert' folder with person folders:
811 811
735 735
Loaded sequence for downtown_crossStreets_00
'downtown_crossStreets_00' contains a 'MotionBert' folder with person folders:
534 534
508 508
Loaded sequence for downtown_downstairs_00
'downtown_downstairs_00' contains a 'MotionBert' folder with person folders:
638 638
Loaded sequence for downtown_enterShop_00
'downtown_enterShop_00' contains a 'M

In [51]:
folders

['E:\\Users\\Philipp\\Dokumente\\Pose_Estimation_3D\\Alphapose\\AlphaPose\\examples\\res\\test_set\\downtown_arguing_00\\MotionBert\\person_1',
 'E:\\Users\\Philipp\\Dokumente\\Pose_Estimation_3D\\Alphapose\\AlphaPose\\examples\\res\\test_set\\downtown_arguing_00\\MotionBert\\person_2',
 'E:\\Users\\Philipp\\Dokumente\\Pose_Estimation_3D\\Alphapose\\AlphaPose\\examples\\res\\test_set\\downtown_bar_00\\MotionBert\\person_1',
 'E:\\Users\\Philipp\\Dokumente\\Pose_Estimation_3D\\Alphapose\\AlphaPose\\examples\\res\\test_set\\downtown_bar_00\\MotionBert\\person_2',
 'E:\\Users\\Philipp\\Dokumente\\Pose_Estimation_3D\\Alphapose\\AlphaPose\\examples\\res\\test_set\\downtown_bus_00\\MotionBert\\person_1',
 'E:\\Users\\Philipp\\Dokumente\\Pose_Estimation_3D\\Alphapose\\AlphaPose\\examples\\res\\test_set\\downtown_bus_00\\MotionBert\\person_2',
 'E:\\Users\\Philipp\\Dokumente\\Pose_Estimation_3D\\Alphapose\\AlphaPose\\examples\\res\\test_set\\downtown_cafe_00\\MotionBert\\person_1',
 'E:\\Users

In [52]:
test_outputs[0]

[{'theta': array([ 1.51890904e-01,  1.69772461e-01,  4.35350910e-02,  6.96666539e-02,
          4.99449782e-02, -1.14527799e-01,  5.32039553e-02, -5.94917722e-02,
          2.58138590e-02,  7.92494044e-02, -2.22851266e-03, -1.49279917e-02,
          1.21975429e-01, -7.02467794e-03, -1.80209451e-03,  1.05426572e-01,
          6.52906392e-03,  6.17518499e-02,  0.00000000e+00, -0.00000000e+00,
          0.00000000e+00, -0.00000000e+00,  0.00000000e+00,  0.00000000e+00,
          0.00000000e+00,  0.00000000e+00, -0.00000000e+00, -1.86795431e-17,
         -2.00576872e-01,  8.68815818e-19,  0.00000000e+00, -0.00000000e+00,
          0.00000000e+00,  0.00000000e+00,  0.00000000e+00,  0.00000000e+00,
          7.02003539e-02,  9.74907365e-04, -6.33319616e-02,  0.00000000e+00,
          0.00000000e+00,  0.00000000e+00,  0.00000000e+00,  0.00000000e+00,
          0.00000000e+00,  0.00000000e+00,  0.00000000e+00,  0.00000000e+00,
          4.17982072e-01, -1.04803964e-01, -1.46291983e+00,  4.3887

In [53]:
print(test_outputs[1])

[{'theta': array([ 1.48716301e-01, -3.94412249e-01,  4.56422009e-03,  1.13056593e-01,
        9.87507328e-02, -1.55325502e-01,  9.63738039e-02, -8.26614574e-02,
        4.53371666e-02,  1.36010591e-02,  7.97581917e-04, -6.46103099e-02,
        9.20671672e-02,  1.07985297e-02, -3.56845334e-02,  1.02180116e-01,
        9.85065475e-03, -7.72889629e-02, -0.00000000e+00,  0.00000000e+00,
        0.00000000e+00,  0.00000000e+00,  0.00000000e+00, -0.00000000e+00,
        0.00000000e+00, -0.00000000e+00,  0.00000000e+00,  5.72743562e-17,
        1.09702200e-01,  6.09719376e-27,  0.00000000e+00,  0.00000000e+00,
       -0.00000000e+00,  0.00000000e+00,  0.00000000e+00,  0.00000000e+00,
        9.10055712e-02,  6.47859573e-02, -7.70338997e-02,  0.00000000e+00,
        0.00000000e+00,  0.00000000e+00,  0.00000000e+00,  0.00000000e+00,
        0.00000000e+00,  0.00000000e+00,  0.00000000e+00,  0.00000000e+00,
        1.38657123e-01,  1.52859334e-02, -1.37375391e+00,  7.69427776e-01,
        3.8834

In [54]:

test_outputs = reorder_list(test_outputs, mapping)

In [55]:
np.asarray(test_outputs).shape

e:\miniconda-envs\motionbert\lib\site-packages\ipykernel_launcher.py:1: VisibleDeprecationWarning: Creating an ndarray from ragged nested sequences (which is a list-or-tuple of lists-or-tuples-or ndarrays with different lengths or shapes) is deprecated. If you meant to do this, you must specify 'dtype=object' when creating the ndarray.
  """Entry point for launching an IPython kernel.


(37,)

In [56]:
# Assuming test_outputs is your array
flattened_array_test_outputs = [dictionary for sublist in test_outputs for dictionary in sublist]


In [57]:
len(flattened_array_test_outputs)

35515

In [58]:
# filtering my outputs according to split_id_test. Like its done for the creation of mesh_val_pw3d

filtered_outputs = []

if DATASET_TYPE == 'test':
    split_ids = split_id_test
elif DATASET_TYPE == 'train':
    split_ids = split_id_train
# Iterate over the ranges
for idx_range in split_ids:
    filtered_outputs.extend(np.asarray(flattened_array_test_outputs)[idx_range])

In [59]:
len(filtered_outputs)

35232

In [60]:
from itertools import islice

# Function to batch a list into chunks of a given size
def batch_dictionaries(flattened_array, batch_size=16):
    batched_output = []
    for i in range(0, len(flattened_array), batch_size):
        batch = flattened_array[i:i + batch_size]
        
        # Combine all entries for the keys 'theta', 'kp_3d', 'verts'
        combined_batch = {
            'theta': [entry['theta'] for entry in batch],
            'kp_3d': [entry['kp_3d'] for entry in batch],
            'verts': [entry['verts'] for entry in batch],
        }
        batched_output.append(combined_batch)
    
    return batched_output

# Usage
batched_array_test_outputs = batch_dictionaries(filtered_outputs)


In [61]:
batched_array_test_outputs = np.asarray(batched_array_test_outputs)

# BATCH OUTPUTS

In [62]:
device = 'cpu'

import torch

# Function to batch dictionaries and move to GPU
def batch_array_of_dicts_to_gpu(array_of_dicts, batch_size, device='cpu'):
    # Initialize batched arrays
    batched_dicts = []
    num_samples = len(array_of_dicts)
    
    for i in range(0, num_samples, batch_size):
        # Slice the dictionaries into batches
        batch = array_of_dicts[i:i + batch_size]
        
        # Initialize a new dictionary for the batch
        batched_dict = {
            'theta': torch.tensor(np.stack([entry['theta'] for entry in batch], axis=0), device=device),  # (batch_size, 16, 82)
            'verts': torch.tensor(np.stack([entry['verts'] for entry in batch], axis=0), device=device),  # (batch_size, 16, 6890, 3)
            'kp_3d': torch.tensor(np.stack([entry['kp_3d'] for entry in batch], axis=0), device=device)   # (batch_size, 16, 17, 3)
        }
        batched_dicts.append(batched_dict)
    
    return batched_dicts


# 1. Saving the batched_output dictionary
def save_batched_output(batched_output, save_path):
    torch.save(batched_output, save_path)
    print(f"Saved batched_output to {save_path}")
    

# 2. Loading the batched_output dictionary and moving to GPU
def load_batched_output(load_path):
    # Load the batched output from the specified path and force CPU loading
    batched_output = torch.load(load_path, map_location="cpu")
    
    # Ensure we are dealing with a list of dictionaries
    if not isinstance(batched_output, list) or not all(isinstance(batch, dict) for batch in batched_output):
        raise ValueError("batched_output should be a list of dictionaries.")
    
    print(f"Loaded batched_output from {load_path} (data is forced to CPU).")
    return batched_output




if SAVE_FILE:

    # Specify the new batch size
    new_batch_size = 128

    # Call the batching function and move data to GPU
    batched_output = batch_array_of_dicts_to_gpu(batched_array_test_outputs, new_batch_size)

    # Check the resulting tensors and their device
    print(batched_output[0]['theta'].shape)  # (128, 16, 82)
    print(batched_output[0]['verts'].shape)  # (128, 16, 6890, 3)
    print(batched_output[0]['kp_3d'].shape)  # (128, 16, 17, 3)

    # Confirm tensors are on the GPU
    print(batched_output[0]['theta'].device)  # cuda:0
    print(batched_output[0]['verts'].device)  # cuda:0
    print(batched_output[0]['kp_3d'].device)  # cuda:0

    save_dir = f'{DATASET_TYPE}_predictions'
    os.makedirs(save_dir, exist_ok=True)

    # File path for saving the output
    save_path = os.path.join(save_dir, 'batched_output.pt')
    save_batched_output(batched_output, save_path)


In [63]:
if not SAVE_FILE:

    save_dir = f'{DATASET_TYPE}_predictions'
    # File path for saving the output
    save_path = os.path.join(save_dir, 'batched_output.pt')

    batched_output = load_batched_output(save_path)

    # Check loaded tensors
    print(batched_output[0]['theta'].shape)  # (128, 16, 82)
    print(batched_output[0]['verts'].shape)  # (128, 16, 6890, 3)
    print(batched_output[0]['kp_3d'].shape)  # (128, 16, 17, 3)

    # Confirm tensors are on GPU
    print(batched_output[-1]['theta'].device)  # cuda:0
    print(batched_output[-1]['verts'].device)  # cuda:0
    print(batched_output[-1]['kp_3d'].device)  # cuda:0

Loaded batched_output from test_predictions\batched_output.pt (data is forced to CPU).
torch.Size([128, 16, 82])
torch.Size([128, 16, 6890, 3])
torch.Size([128, 16, 17, 3])
cpu
cpu
cpu


In [64]:
print(batched_output[-1]['theta'].device)  # cuda:0
print(batched_output[-1]['verts'].device)  # cuda:0
print(batched_output[-1]['kp_3d'].device)  # cuda:0

cpu
cpu
cpu


In [65]:
################### len(batched_output) ##############


In [66]:
#Save predictions

In [67]:
# sum = 0

# for i in range(len(mesh_val_pw3d)):
#     sum += len(mesh_val_pw3d[i][1]['theta'])

# print(sum)

In [68]:
########################################################
########################################################
########################################################
########################################################

########################################################
########################################################
########################################################
########################################################

In [69]:
len(batched_array_test_outputs)

2202

In [70]:
# total_length = sum(len(output) for output in t
# est_outputs)  #test_outputs are ALL outputs
# print(f"Total length: {total_length}")


In [71]:
# in mesh_val_pw3d[0][i] there are dictionaries with batches of length 16 with all the gt thetas, verts and kp3d

In [72]:
# mesh_train_pw3d = MotionSMPL(args, data_split='train', dataset="pw3d")
# train_loader_pw3d = DataLoader(mesh_train_pw3d, **trainloader_params)

# mesh_val_pw3d = MotionSMPL(args, data_split='test', dataset="pw3d")
# test_loader_pw3d = DataLoader(mesh_val_pw3d, **testloader_params)

In [73]:
i = 0  # Index of the batch you want to get

# Create a new iterator from the dataloader
test_loader_iter = iter(test_loader_pw3d)

# Access the ith batch
batch = None
for idx, (data, target) in enumerate(test_loader_iter):
    if idx == i:
        batch = (data, target)
        break

# If the batch is not found, raise an error
if batch is None:
    raise IndexError("Batch index out of range.")

input_gt, batch_gt = batch


In [74]:
dataset_pw3d['test']['source'][14336]

'downtown_walkBridge_010'

In [75]:
pred = batched_output[0]['kp_3d'][0:50]
gt = batch_gt['kp_3d'][0:50]

gt = gt.reshape(800, 17, 3)
pred = pred.reshape(800, 17, 3)


In [76]:
# scaling_factor = 1000.0

# # Scale the coordinates, keeping the middle coordinate fixed at (0, 0, 0)
# middle_index = 0  # Assuming middle coordinate is in the center of the 17 points
# for frame in pred:
#     for i, coord in enumerate(frame):
#         if i != middle_index:  # Skip scaling the fixed middle coordinate
#             frame[i] *= scaling_factor

In [77]:
# Create the directory if it doesn't exist
output_dir = 'regressed_coordinates/batched'
os.makedirs(output_dir, exist_ok=True)

# Save the pred tensor as a .npy file
np.save(os.path.join(output_dir, 'pred.npy'), pred.numpy())  # Convert tensor to numpy array before saving

# Save the ground truth as a .npy file
np.save(os.path.join(output_dir, 'gt.npy'), gt)

## WHOLE DATASET

In [78]:
def validate(test_loader, criterion, dataset_name='h36m'):
    #model.eval()
    print(f'===========> validating {dataset_name}')
    batch_time = AverageMeter()
    losses = AverageMeter()
    losses_dict = {'loss_3d_pos': AverageMeter(), 
                   'loss_3d_scale': AverageMeter(), 
                   'loss_3d_velocity': AverageMeter(),
                   'loss_lv': AverageMeter(), 
                   'loss_lg': AverageMeter(), 
                   'loss_a': AverageMeter(), 
                   'loss_av': AverageMeter(), 
                   'loss_pose': AverageMeter(), 
                   'loss_shape': AverageMeter(),
                   'loss_norm': AverageMeter(),
    }
    mpjpes = AverageMeter()
    mpves = AverageMeter()
    results = defaultdict(list)
    smpl = SMPL(args.data_root, batch_size=1).cuda()
    J_regressor = smpl.J_regressor_h36m
    with torch.no_grad():
        end = time.time()
        for idx, (batch_input, batch_gt) in tqdm(enumerate(test_loader)):
            batch_size, clip_len = batch_input.shape[:2]
            if torch.cuda.is_available():
                batch_gt['theta'] = batch_gt['theta'].cuda().float()
                batch_gt['kp_3d'] = batch_gt['kp_3d'].cuda().float()
                batch_gt['verts'] = batch_gt['verts'].cuda().float()
                batch_input = batch_input.cuda().float()

            predictions_batch = batched_output[idx]
            predictions_batch['theta'] = predictions_batch['theta'].cuda().float()
            predictions_batch['kp_3d'] = predictions_batch['kp_3d'].cuda().float()
            predictions_batch['verts'] = predictions_batch['verts'].cuda().float()


            output = [predictions_batch]

            output_final = output
            output_final = output

            loss_dict = criterion(output, batch_gt)
            loss = args.lambda_3d      * loss_dict['loss_3d_pos']      + \
                   args.lambda_scale   * loss_dict['loss_3d_scale']    + \
                   args.lambda_3dv     * loss_dict['loss_3d_velocity'] + \
                   args.lambda_lv      * loss_dict['loss_lv']          + \
                   args.lambda_lg      * loss_dict['loss_lg']          + \
                   args.lambda_a       * loss_dict['loss_a']           + \
                   args.lambda_av      * loss_dict['loss_av']          + \
                   args.lambda_shape   * loss_dict['loss_shape']       + \
                   args.lambda_pose    * loss_dict['loss_pose']        + \
                   args.lambda_norm    * loss_dict['loss_norm'] 
            # update metric
            losses.update(loss.item(), batch_size)
            loss_str = ''
            for k, v in loss_dict.items():
                losses_dict[k].update(v.item(), batch_size)
                loss_str += '{0} {loss.val:.3f} ({loss.avg:.3f})\t'.format(k, loss=losses_dict[k])
            mpjpe, mpve = compute_error(output, batch_gt)
            mpjpes.update(mpjpe, batch_size)
            mpves.update(mpve, batch_size)
            
            for keys in output[0].keys():
                output[0][keys] = output[0][keys].detach().cpu().numpy()
                batch_gt[keys] = batch_gt[keys].detach().cpu().numpy()
            results['kp_3d'].append(output[0]['kp_3d'])
            results['verts'].append(output[0]['verts'])
            results['kp_3d_gt'].append(batch_gt['kp_3d'])
            results['verts_gt'].append(batch_gt['verts'])

            # measure elapsed time
            batch_time.update(time.time() - end)
            end = time.time()

            if idx % int(100) == 0:
                print('Test: [{0}/{1}]\t'
                      'Time {batch_time.val:.3f} ({batch_time.avg:.3f})\t'
                      'Loss {loss.val:.4f} ({loss.avg:.4f})\t'
                      '{2}'
                      'PVE {mpves.val:.3f} ({mpves.avg:.3f})\t'
                      'JPE {mpjpes.val:.3f} ({mpjpes.avg:.3f})'.format(
                       idx, len(test_loader), loss_str, batch_time=batch_time,
                       loss=losses, mpves=mpves, mpjpes=mpjpes))

    print(f'==> start concating results of {dataset_name}')
    for term in results.keys():
        results[term] = np.concatenate(results[term])
    print(f'==> start evaluating {dataset_name}...')
    error_dict = evaluate_mesh(results)
    err_str = ''
    for err_key, err_val in error_dict.items():
        err_str += '{}: {:.2f}mm \t'.format(err_key, err_val)
    print(f'=======================> {dataset_name} validation done: ', loss_str)
    print(f'=======================> {dataset_name} validation done: ', err_str)
    return losses.avg, error_dict['mpjpe'], error_dict['pa_mpjpe'], error_dict['mpve'], losses_dict

In [79]:
criterion = MeshLoss(loss_type = args.loss_type)

In [80]:
if DATASET_TYPE == 'test':
    loader = test_loader_pw3d
if DATASET_TYPE == 'train':
    loader = train_loader_pw3d

test_loss, test_mpjpe, test_pa_mpjpe, test_mpve, test_losses_dict = validate(loader, criterion=criterion, dataset_name='3dpw')

===========> validating 3dpw


1it [00:04,  4.29s/it]

Test: [0/18]	Time 4.295 (4.295)	Loss 291.0266 (291.0266)	loss_3d_pos 110.024 (110.024)	loss_3d_scale 90.511 (90.511)	loss_3d_velocity 4.738 (4.738)	loss_lv 2.514 (2.514)	loss_lg 20.836 (20.836)	loss_a 0.143 (0.143)	loss_av 0.010 (0.010)	loss_shape 0.591 (0.591)	loss_pose 0.130 (0.130)	loss_norm 2.909 (2.909)	PVE 455.367 (455.367)	JPE 110.024 (110.024)


18it [00:31,  1.75s/it]


==> start concating results of 3dpw
==> start evaluating 3dpw...
=======================> 3dpw validation done:  loss_3d_pos 88.941 (107.262)	loss_3d_scale 82.827 (100.458)	loss_3d_velocity 3.124 (7.957)	loss_lv 1.072 (9.417)	loss_lg 10.569 (15.509)	loss_a 0.115 (0.154)	loss_av 0.005 (0.013)	loss_shape 0.732 (0.730)	loss_pose 0.120 (0.141)	loss_norm 3.356 (3.397)	
=======================> 3dpw validation done:  mpve: 472.70mm 	mpjpe: 119.04mm 	pa_mpjpe: 72.22mm 	mpjpe_17j: 107.26mm 	pa_mpjpe_17j: 68.65mm 	


In [83]:
# RESULT: THE ERROR HAS TO BE IN THE EXTRACTION OF THE VERTICES!!! So compare vertices.npy and all_frames_vertices.npy

# OKAY, I have to use the other way of extracting the vertices

In [136]:
# Create a new iterator to reset the DataLoader
data_iter = iter(test_loader_pw3d)

# Fetch the first batch to verify it starts from the beginning
first_batch = next(data_iter)



Reset and fetched the first batch.


In [135]:
first_element['verts'].shape

torch.Size([128, 16, 6890, 3])